https://pycaret.gitbook.io/docs/learn-pycaret/official-blog/multiple-time-series-forecasting-with-pycaret

In [1]:
from pycaret.regression import *

import pandas as pd
from pandas import Series, DataFrame
import numpy as np
import category_encoders as ce

# Visualization
import matplotlib.pylab as plt
from matplotlib import font_manager, rc
import matplotlib
import seaborn as sns
import plotly.express as px
%matplotlib inline
matplotlib.rcParams['font.family'] = 'Malgun Gothic'
# Preprocessing & Feature Engineering
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler, LabelEncoder
from sklearn.impute import SimpleImputer 
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import PowerTransformer
from sklearn.feature_selection import SelectPercentile

# Hyperparameter Optimization
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV

# Modeling
from sklearn.dummy import DummyClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import ExtraTreesClassifier
from sklearn.ensemble import GradientBoostingClassifier
from xgboost import XGBClassifier, XGBRegressor, XGBRFRegressor
from lightgbm import LGBMClassifier
from sklearn.svm import SVC
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import StackingClassifier
from sklearn.base import ClassifierMixin

# PyTorch
# import torch
# from torch.utils.data import Dataset, DataLoader, TensorDataset
# import torch.nn as nn
# import torch.nn.functional as F
# import torch.optim as optim
# from torch.autograd import Variable
# from torch.nn import Parameter
# from torch import Tensor
# from torch.utils.data import DataLoader

# Evaluation
from sklearn.metrics import roc_auc_score
from sklearn.metrics import accuracy_score
from sklearn.model_selection import cross_val_score
from sklearn.metrics import log_loss

# Utility
import os
import time
import datetime
import random
import warnings; warnings.filterwarnings("ignore")
from IPython.display import Image
import pickle
from tqdm import tqdm
import platform
from itertools import combinations
from scipy.stats.mstats import gmean

# from bayes_opt import BayesianOptimization
# from num2words import num2words
import statsmodels.api as sm
import statsmodels.formula.api as smf
from statsmodels.stats.outliers_influence import OLSInfluence

In [2]:
train = pd.read_csv('../data/train.csv')
test = pd.read_csv('../data/test.csv')
inter = pd.read_csv('../data/international_trade.csv')
submit = pd.read_csv('../data/sample_submission.csv')

# train.drop(columns = 'ID', inplace = True)
# test.drop(columns = 'ID', inplace = True)

In [3]:
train

ID   timestamp item corporation location  supply(kg)  \
0      TG_A_J_20190101  2019-01-01   TG           A        J         0.0   
1      TG_A_J_20190102  2019-01-02   TG           A        J         0.0   
2      TG_A_J_20190103  2019-01-03   TG           A        J     60601.0   
3      TG_A_J_20190104  2019-01-04   TG           A        J     25000.0   
4      TG_A_J_20190105  2019-01-05   TG           A        J     32352.0   
...                ...         ...  ...         ...      ...         ...   
59392  RD_F_J_20230227  2023-02-27   RD           F        J    452440.0   
59393  RD_F_J_20230228  2023-02-28   RD           F        J    421980.0   
59394  RD_F_J_20230301  2023-03-01   RD           F        J    382980.0   
59395  RD_F_J_20230302  2023-03-02   RD           F        J    477220.0   
59396  RD_F_J_20230303  2023-03-03   RD           F        J    427520.0   

       price(원/kg)  
0              0.0  
1              0.0  
2           1728.0  
3           1408.0  
4           1250.0  
...            ...  
59392        468.0  
59393        531.0  
59394        574.0  
59395        523.0  
59396        529.0  

[59397 rows x 7 columns]

In [3]:
train = train.rename(columns={'supply(kg)':'supply','price(원/kg)':'price'})
train.columns

Index(['ID', 'timestamp', 'item', 'corporation', 'location', 'supply',
       'price'],
      dtype='object')

In [4]:
# prepare the data
'''
0. item, location. corporation을 LabelEncoding한다.
1. item, location, corporation 을 time-series 컬럼으로 결합한다.
2. timestamp로부터 month, year, day, dayofweek 를 추출
'''

data = train.copy()
test_ = test.copy()
data['timestamp'] = pd.to_datetime(data['timestamp'])
test_['timestamp'] = pd.to_datetime(test_['timestamp'])

# 0.
encoders = {}
for col in ['item','location','corporation']:
    encoder = LabelEncoder()
    data[col] = encoder.fit_transform(data[col])
    test_[col] = encoder.transform(test_[col])
    encoders[col] = encoder

# 1.
data['item_'] = ['item_' + str(i) for i in data['item']]
data['location_'] = ['location_' + str(i) for i in data['location']]
data['corporation_'] = ['corporation_' + str(i) for i in data['corporation']]
data['time_series'] = data[['item_'
                            , 'corporation_','location_'
                           ]].apply(lambda x: '_'.join(x), axis=1)
data.drop(['item_', 'corporation_','location_'], axis=1, inplace=True)
test_['item_'] = ['item_' + str(i) for i in test_['item']]
test_['location_'] = ['location_' + str(i) for i in test_['location']]
test_['corporation_'] = ['corporation_' + str(i) for i in test_['corporation']]
test_['time_series'] = test_[['item_'
                            , 'corporation_','location_'
                           ]].apply(lambda x: '_'.join(x), axis=1)
test_.drop(['item_', 'corporation_','location_'], axis=1, inplace=True)


# 2.
data['year'] = data['timestamp'].dt.year
data['month'] = data['timestamp'].dt.month
data['day'] = data['timestamp'].dt.day
data['dow'] = data['timestamp'].dt.dayofweek
data['doy'] = data['timestamp'].dt.dayofyear
test_['year'] = test_['timestamp'].dt.year
test_['month'] = test_['timestamp'].dt.month
test_['day'] = test_['timestamp'].dt.day
test_['dow'] = test_['timestamp'].dt.dayofweek
test_['doy'] = test_['timestamp'].dt.dayofyear

data.head(3)


ID  timestamp  item  corporation  location   supply   price  \
0  TG_A_J_20190101 2019-01-01     4            0         0      0.0     0.0   
1  TG_A_J_20190102 2019-01-02     4            0         0      0.0     0.0   
2  TG_A_J_20190103 2019-01-03     4            0         0  60601.0  1728.0   

                       time_series  year  month  day  dow  doy  
0  item_4_corporation_0_location_0  2019      1    1    1    1  
1  item_4_corporation_0_location_0  2019      1    2    2    2  
2  item_4_corporation_0_location_0  2019      1    3    3    3

In [6]:
test_.head(3)

ID  timestamp  item  corporation  location  \
0  TG_A_J_20230304 2023-03-04     4            0         0   
1  TG_A_J_20230305 2023-03-05     4            0         0   
2  TG_A_J_20230306 2023-03-06     4            0         0   

                       time_series  year  month  day  dow  doy  
0  item_4_corporation_0_location_0  2023      3    4    5   63  
1  item_4_corporation_0_location_0  2023      3    5    6   64  
2  item_4_corporation_0_location_0  2023      3    6    0   65

In [9]:
categorical_cols = ['month','dow','item','corporation','location']
numeric_cols = ['year','day','doy']
timestamp_col = 'timestamp'
target_col = 'price'
ignore_cols = ['ID','timestamp','supply','time_series']

all_results = []
final_models = {}
all_ts = data['time_series'].unique()

for i in tqdm(all_ts):
    df_subset = data[data['time_series']==i]
    s = setup(data=df_subset,
              target=target_col,
              session_id=123,
              train_size=0.8,
              categorical_features=categorical_cols,
              ignore_features=ignore_cols,
              numeric_features=numeric_cols,
              normalize=True,
              normalize_method='minmax',
              fold_strategy='timeseries',
              fold=5,
              fold_shuffle=False,
              data_split_shuffle=False,
              transform_target=True,
              transform_target_method='yeo-johnson',
              remove_outliers=False,
              remove_multicollinearity=True,
              multicollinearity_threshold=0.9,
              verbose=False,
              use_gpu = True
             )
    
    best_model = compare_models(sort='RMSE',verbose=True)
    
    p = pull().iloc[0:1]
    p['time_series'] = str(i)
    all_results.append(p)
    
    f = finalize_model(best_model)
    
    final_models[i] = f
    
    save_model(f, model_name=f'../models/pycaret_regression_{i}')
    


  0%|                                                                    | 0/39 [00:00<?, ?it/s]

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 2, number of used features: 0
[LightGBM] [Info] Using GPU Device: gfx1035, Vendor: Advanced Micro Devices, Inc.
[LightGBM] [Info] Compiling OpenCL Kernel with 16 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Warning] GPU acceleration is disabled because no non-trivial dense features can be found
[LightGBM] [Info] Start training from score 0.500000
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 2, number of used features: 0
[LightGBM] [Info] Using GPU Device: gfx1035, Vendor: Advanced Micro Devices, Inc.
[LightGBM] [Info] Compiling OpenCL Kernel with 16 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Warning] GPU acceleration is disabled because no non-trivial dense features can be found
[LightGBM] [Info] Start training from score 0.500000
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 2, number of used features: 0
[LightGBM] [Info] Using GPU Device: gfx1035, Vendor: Advanced Micro Devices, Inc.
[LightGBM] [Info] Compiling OpenCL Kernel with 16 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Warning] GPU acceleration is disabled because no non-trivial dense features can be found
[LightGBM] [Info] Start training from score 0.500000
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 2, number of used features: 0
[LightGBM] [Info] Using GPU Device: gfx1035, Vendor: Advanced Micro Devices, Inc.
[LightGBM] [Info] Compiling OpenCL Kernel with 16 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Warning] GPU acceleration is disabled because no non-trivial dense features can be found
[LightGBM] [Info] Start training from score 0.500000
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves

...

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 2, number of used features: 0
[LightGBM] [Info] Using GPU Device: gfx1035, Vendor: Advanced Micro Devices, Inc.
[LightGBM] [Info] Compiling OpenCL Kernel with 16 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Warning] GPU acceleration is disabled because no non-trivial dense features can be found
[LightGBM] [Info] Start training from score 0.500000
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 2, number of used features: 0
[LightGBM] [Info] Using GPU Device: gfx1035, Vendor: Advanced Micro Devices, Inc.
[LightGBM] [Info] Compiling OpenCL Kernel with 16 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Warning] GPU acceleration is disabled because no non-trivial dense features can be found
[LightGBM] [Info] Start training from score 0.500000
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 2, number of used features: 0
[LightGBM] [Info] Using GPU Device: gfx1035, Vendor: Advanced Micro Devices, Inc.
[LightGBM] [Info] Compiling OpenCL Kernel with 16 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Warning] GPU acceleration is disabled because no non-trivial dense features can be found
[LightGBM] [Info] Start training from score 0.500000
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves

100%|████████████████████████████████████████████████████████| 39/39 [1:57:20<00:00, 180.53s/it]

Transformation Pipeline and Model Successfully Saved


In [10]:
concat_results = pd.concat(all_results,axis=0)
concat_results

Model        MAE           MSE       RMSE  \
et                  Extra Trees Regressor  1955.0918  1.029822e+07  2840.3522   
rf                Random Forest Regressor  1044.7801  2.667156e+06  1504.6214   
et                  Extra Trees Regressor  1526.8809  5.684708e+06  2323.5348   
gbr           Gradient Boosting Regressor  1109.6962  2.900771e+06  1590.9329   
rf                Random Forest Regressor  1672.4773  7.560149e+06  2654.2123   
rf                Random Forest Regressor  1103.6202  3.171177e+06  1706.2086   
huber                     Huber Regressor  1425.1436  5.028272e+06  2174.7673   
ada                    AdaBoost Regressor  1417.4589  4.284480e+06  1960.7388   
huber                     Huber Regressor  1514.8503  5.821247e+06  2275.8417   
gbr           Gradient Boosting Regressor  1279.1147  4.010869e+06  1846.4418   
lar                Least Angle Regression   217.5302  2.870547e+05   442.0626   
gbr           Gradient Boosting Regressor    57.9069  8.927503e+04   219.3533   
gbr           Gradient Boosting Regressor   111.2836  1.932057e+05   322.7098   
lightgbm  Light Gradient Boosting Machine    88.8456  1.228570e+05   214.4524   
lr                      Linear Regression    10.2683  2.959915e+03    24.3323   
lightgbm  Light Gradient Boosting Machine    85.1477  1.109730e+05   198.5956   
lar                Least Angle Regression    21.2012  2.238126e+04    86.9444   
lightgbm  Light Gradient Boosting Machine    17.2870  1.193089e+04    69.0698   
lasso                    Lasso Regression     2.1871  1.410173e+03    20.1650   
xgboost         Extreme Gradient Boosting    45.8621  4.583690e+04   123.7576   
xgboost         Extreme Gradient Boosting    29.8646  2.675975e+04    73.1570   
rf                Random Forest Regressor   136.1159  8.172085e+04   273.3344   
xgboost         Extreme Gradient Boosting    82.7621  6.759385e+04   163.6613   
lar                Least Angle Regression     0.4121  1.672344e+02     5.7892   
rf                Random Forest Regressor   120.5787  5.939894e+04   231.0101   
et                  Extra Trees Regressor   111.8506  5.140829e+04   217.0722   
xgboost         Extreme Gradient Boosting    11.7441  5.405895e+03    32.8813   
xgboost         Extreme Gradient Boosting    24.7190  2.487301e+04    70.5309   
huber                     Huber Regressor   823.9814  2.336338e+06  1421.0224   
lar                Least Angle Regression   757.8016  2.841650e+06  1153.3744   
par          Passive Aggressive Regressor   119.3155  3.292683e+05   256.6197   
xgboost         Extreme Gradient Boosting    15.1172  3.870377e+04   118.5667   
lar                Least Angle Regression   438.0308  1.338052e+06   719.7652   
lasso                    Lasso Regression    36.2269  1.061206e+05   198.3801   
dt                Decision Tree Regressor   603.0216  1.528505e+06  1132.7491   
dt                Decision Tree Regressor   705.0896  1.978908e+06  1286.1509   
lar                Least Angle Regression   726.7862  2.613986e+06  1174.8001   
dt                Decision Tree Regressor   157.7940  9.640060e+04   297.6184   
br                         Bayesian Ridge   134.3515  6.229113e+04   221.8008   

              R2   RMSLE    MAPE  TT (Sec)                      time_series  
et       -0.4377  3.6766  0.7140     0.220  item_4_corporation_0_location_0  
rf        0.3755  1.7938  0.4266     0.252  item_4_corporation_0_location_1  
et        0.1793  2.4092  0.5506     0.222  item_4_corporation_1_location_0  
gbr       0.3355  1.9370  0.4194     0.152  item_4_corporation_1_location_1  
rf        0.1861  2.1800  0.5434     0.250  item_4_corporation_2_location_0  
rf        0.3198  1.7169  0.3910     0.316  item_4_corporation_2_location_1  
huber     0.1194  2.6741  0.5515     0.122  item_4_corporation_3_location_0  
ada       0.2269  1.7912  0.4270     0.162  item_4_corporation_3_location_1  
huber     0.0153  3.0425  0.4618     0.106  item_4_corporation_4_location_0  
gbr       0.133

In [5]:
all_scores = []
test_features = ['item','corporation','location','year','month','day','dow','doy']

for i in tqdm(data['time_series'].unique()):
    test_subset = test_[test_['time_series']==i]
    test_subset = test_subset[test_features]
    l = load_model(f'../models/pycaret_regression_{i}',verbose=False)
    p = predict_model(l,data=test_subset)
    p['time_series']=i
    all_scores.append(p)

concat_df = pd.concat(all_scores,axis=0)
concat_df


100%|███████████████████████████████████████████████████████████| 39/39 [00:10<00:00,  3.58it/s]


item  corporation  location  year  month  day  dow  doy  \
0        4            0         0  2023      3    4    5   63   
1        4            0         0  2023      3    5    6   64   
2        4            0         0  2023      3    6    0   65   
3        4            0         0  2023      3    7    1   66   
4        4            0         0  2023      3    8    2   67   
...    ...          ...       ...   ...    ...  ...  ...  ...   
1087     3            5         0  2023      3   27    0   86   
1088     3            5         0  2023      3   28    1   87   
1089     3            5         0  2023      3   29    2   88   
1090     3            5         0  2023      3   30    3   89   
1091     3            5         0  2023      3   31    4   90   

      prediction_label                      time_series  
0          4374.717606  item_4_corporation_0_location_0  
1             0.000000  item_4_corporation_0_location_0  
2          3531.892550  item_4_corporation_0_location_0  
3          2978.573759  item_4_corporation_0_location_0  
4          3317.646750  item_4_corporation_0_location_0  
...                ...                              ...  
1087        424.031780  item_3_corporation_5_location_0  
1088        418.857285  item_3_corporation_5_location_0  
1089        389.916084  item_3_corporation_5_location_0  
1090        383.990342  item_3_corporation_5_location_0  
1091        353.032458  item_3_corporation_5_location_0  

[1092 rows x 10 columns]

In [7]:
pred = concat_df['prediction_label'].apply(lambda x:x if x>=0 else 0)
np.float32(pred.values)

array([4374.718  ,    0.     , 3531.8926 , ...,  389.91608,  383.99036,
        353.03247], dtype=float32)

In [8]:
submit['answer'] = pred.values
submit

ID       answer
0     TG_A_J_20230304  4374.717606
1     TG_A_J_20230305     0.000000
2     TG_A_J_20230306  3531.892550
3     TG_A_J_20230307  2978.573759
4     TG_A_J_20230308  3317.646750
...               ...          ...
1087  RD_F_J_20230327   424.031780
1088  RD_F_J_20230328   418.857285
1089  RD_F_J_20230329   389.916084
1090  RD_F_J_20230330   383.990342
1091  RD_F_J_20230331   353.032458

[1092 rows x 2 columns]

In [22]:
submit[submit['answer']>10000]

ID        answer
367  CR_D_J_20230307  6.802243e+04
368  CR_D_J_20230308  1.667799e+05
369  CR_D_J_20230309  9.034267e+04
422  CR_E_J_20230306  9.561909e+04
423  CR_E_J_20230307  1.907358e+04
424  CR_E_J_20230308  3.161907e+04
425  CR_E_J_20230309  2.110016e+04
429  CR_E_J_20230313  1.348560e+04
431  CR_E_J_20230315  1.057163e+04
432  CR_E_J_20230316  1.002527e+04
840  BC_B_J_20230304  1.874774e+04
843  BC_B_J_20230307  4.304399e+10
847  BC_B_J_20230311  3.419387e+05
849  BC_B_J_20230313  3.934077e+04
854  BC_B_J_20230318  1.751344e+09
856  BC_B_J_20230320  1.470146e+06
858  BC_B_J_20230322  7.145186e+04
865  BC_B_J_20230329  5.797301e+06

In [21]:
submit.set_index('ID').to_csv('../data/pycaret_231115_1903.csv')

In [73]:
best = compare_models(sort='RMSE')

In [76]:
created = create_model('catboost',target='price',experiment_custom_tags=s)

Initiated  . . . . . . . . . . . . . . . . . .             14:35:03
Status     . . . . . . . . . . . . . . . . . .  Selecting Estimator
Estimator  . . . . . . . . . . . . . . . . . .    Compiling Library

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

TypeError: __init__() got an unexpected keyword argument 'target'

In [89]:
best_top3 = compare_models(sort='RMSE',n_select=3)

In [90]:
best_top3

[]

In [ ]:
# finalize
f = finalize_model(
#     best
    created
    )


In [ ]:
### 임시

# 0.
test_=test.copy()
encoders = {}
for col in ['item','location','corporation']:
    encoder = encoders[col]
    test_[col] = encoder.transform(test_[col])

# 1.
test_['item_'] = ['item_' + str(i) for i in test_['item']]
test_['location_'] = ['location_' + str(i) for i in test_['location']]
test_['corporation_'] = ['corporation_' + str(i) for i in test_['corporation']]
test_['time_series'] = test_[['item_'
                            , 'corporation_','location_'
                           ]].apply(lambda x: '_'.join(x), axis=1)
test_.drop(['item_', 'corporation_','location_'], axis=1, inplace=True)

# 2.
test_['year'] = test_['timestamp'].dt.year
test_['month'] = test_['timestamp'].dt.month
test_['day'] = test_['timestamp'].dt.day
test_['dow'] = test_['timestamp'].dt.dayofweek
test_['doy'] = test_['timestamp'].dt.dayofyear

test_.head(3)


In [ ]:
test_for_pred = test_.drop(['ID','timestamp',''])

In [ ]:
p = predict_model(f,data=test_for_pred)
p